# GNNExplaner

著者のコードをGoogle Driveにあげて, 実行しています.

## Google Driveをマウント, tensorboardXのインストール

In [0]:
from google.colab import drive
drive.mount('/content/drive',force_remount=True)

Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3aietf%3awg%3aoauth%3a2.0%3aoob&response_type=code&scope=email%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdocs.test%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive%20https%3a%2f%2fwww.googleapis.com%2fauth%2fdrive.photos.readonly%20https%3a%2f%2fwww.googleapis.com%2fauth%2fpeopleapi.readonly

Enter your authorization code:
··········
Mounted at /content/drive


In [0]:
!pwd

/content


In [52]:
!ls "/content/drive/My Drive/gnn-model-explainer-master/"

CHANGELOG.md	   explain_pyg.py   main.py	   README.md
configs.py	   gengraph.py	    models.py	   requirements.txt
example.sh	   INSTALLATION.md  models_pyg.py  train.py
explainer_main.py  LICENSE	    __pycache__    utils


In [49]:
!pip install tensorboardX

## GNNの学習

In [0]:
!python3 "/content/drive/My Drive/gnn-model-explainer-master/train.py" --help

In [0]:
!python3 "/content/drive/My Drive/gnn-model-explainer-master/train.py" --dataset=syn1 --gpu

## GNNExplainerの学習

In [0]:
!python "/content/drive/My Drive/gnn-model-explainer-master/explainer_main.py" --help

In [87]:
!python "/content/drive/My Drive/gnn-model-explainer-master/explainer_main.py" --explain-node=300 --dataset=syn1

Using CPU
loading model
ckpt/syn1_base_h20_o20.pth.tar
=> loading checkpoint 'ckpt/syn1_base_h20_o20.pth.tar'
Loaded model from ckpt
input dim:  10 ; num classes:  4
Method:  base
node label:  1
neigh graph idx:  300 198
Node predicted label:  1
epoch:  0 ; loss:  174.8980255126953 ; mask density:  0.7103129625320435 ; pred:  tensor([0.0605, 0.8029, 0.1168, 0.0198], grad_fn=<SoftmaxBackward>)
log/mask/graphsyn1_base_h20_o20_explain_0.pdf
log/grad/graphsyn1_base_h20_o20_explain_0.pdf
epoch:  1 ; loss:  170.05203247070312 ; mask density:  0.6897938251495361 ; pred:  tensor([0.0286, 0.8742, 0.0851, 0.0121], grad_fn=<SoftmaxBackward>)
epoch:  2 ; loss:  165.12005615234375 ; mask density:  0.6683581471443176 ; pred:  tensor([0.0349, 0.8463, 0.1032, 0.0157], grad_fn=<SoftmaxBackward>)
epoch:  3 ; loss:  159.96658325195312 ; mask density:  0.6461001038551331 ; pred:  tensor([0.0381, 0.8359, 0.1087, 0.0172], grad_fn=<SoftmaxBackward>)
epoch:  4 ; loss:  154.59957885742188 ; mask density:  0.62

## Tensorboardで確認

In [84]:
%load_ext tensorboard

The tensorboard extension is already loaded. To reload it, use:
  %reload_ext tensorboard


In [85]:
%tensorboard --logdir ./log

Reusing TensorBoard on port 6006 (pid 2360), started 0:34:50 ago. (Use '!kill 2360' to kill it.)

In [0]:
!kill 2360

## 可視化する

In [0]:
from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets


import numpy as np
import os
import networkx as nx
import matplotlib.pyplot as plt
import json

%matplotlib inline

In [81]:
logdir = "log/"
#expdir = 'syn1_base_h20_o20'
dirs = os.listdir(os.path.join(logdir))
dirs

['mask',
 'syn1_base_h20_o20',
 'syn1_base_h20_o20_explain',
 'grad',
 'masked_adj_syn1_base_h20_o20_explainnode_idx_300graph_idx_-1.npy']

In [82]:
masks = []
# This would print all the files and directories
for file in dirs:
    if file.split('.')[-1] == 'npy':
        print(file)
        masks.append(file)
masks

masked_adj_syn1_base_h20_o20_explainnode_idx_300graph_idx_-1.npy


['masked_adj_syn1_base_h20_o20_explainnode_idx_300graph_idx_-1.npy']

In [70]:
from networkx.readwrite import json_graph

def save_mask(G, fname, fmt='json', suffix=''):
    pth = os.path.join(logdir, expdir, fname+'-filt-'+suffix+'.'+fmt)
    if fmt == 'json':
        dt = json_graph.node_link_data(G)
        with open(pth, 'w') as f:
            json.dump(dt, f)
    elif fmt == 'pdf':
        plt.savefig(pth)
    elif fmt == 'npy':
        np.save(pth, nx.to_numpy_array(G))
  

def show_adjacency_full(mask, ax=None):
    adj = np.load(os.path.join(logdir, mask), allow_pickle=True)
    if ax is None:
        plt.figure()
        plt.imshow(adj);
    else:
        ax.imshow(adj)
    return adj

def read_adjacency_full(mask, ax=None):
    adj = np.load(os.path.join(logdir,mask), allow_pickle=True)
    return adj

filt_adj = read_adjacency_full(masks[5])
@interact
def filter_adj(thresh=0.5):
    filt_adj[filt_adj<thresh] = 0
    return filt_adj

interactive(children=(FloatSlider(value=0.5, description='thresh', max=1.5, min=-0.5), Output()), _dom_classes…

In [93]:
# EDIT THIS INDEX
MASK_IDX = 0
# EDIT THIS INDEX

m = masks[MASK_IDX]
adj = read_adjacency_full(m)


@interact(thresh=widgets.FloatSlider(value=0.5, min=0.0, max=1.0, step=0.01))
def plot_interactive(thresh=0.5):
    filt_adj = read_adjacency_full(m)
    fig, (ax1, ax2, ax3) = plt.subplots(1, 3, figsize=(15,5))
    plt.title(str(m));

    # Full adjacency
    ax1.set_title('Full Adjacency mask')
    adj = show_adjacency_full(m, ax=ax1);
    
    # Filtered adjacency
    filt_adj[filt_adj<thresh] = 0
    ax2.set_title('Filtered Adjacency mask');
    ax2.imshow(filt_adj);
    
    # Plot subgraph
    ax3.set_title("Subgraph")
    G_ = nx.from_numpy_array(adj)
    G  = nx.from_numpy_array(filt_adj)
    G.remove_nodes_from(list(nx.isolates(G)))
    nx.draw(G, ax=ax3)
    save_mask(G, fname=m, fmt='json')
    
    print("Removed {} edges -- K = {} remain.".format(G_.number_of_edges()-G.number_of_edges(), G.number_of_edges()))
    print("Removed {} nodes -- K = {} remain.".format(G_.number_of_nodes()-G.number_of_nodes(), G.number_of_nodes()))

interactive(children=(FloatSlider(value=0.5, description='thresh', max=1.0, step=0.01), Output()), _dom_classe…